## Objetivo y alcance




Para esta materia el objetivo es poder hacer un primer acercamiento a un proceso de aprendizaje supervisado.

En este laboratorio no se espera que se encuentre el mejor modelo con sus mejores parámetros, sino que se logre la buena práctica de realizar los pasos necesarios en un proceso de aprendizaje supervisado, desde el entendimiento de la pregunta de investigación hasta la preparación de datos, desde la división del dataset hasta la evaluación del modelo. Para realizar el práctico vamos a utilizar el datasets que hayan generado en el práctico anterior.


## Introducción
En un mismo día une operadore humano de una clínica responde cientos de consultas sobre problemáticas increiblemente sensibles como lo es la salud de una persona y las preocupaciones relacionadas a eso. Además la demanda de trabajo de une operadore humano es multivariada y dinámica: algunos días hay un flujo mayor de pacientes usando los sistemas hospitalarios, y hay momentos del mes y del día en donde prácticamente no hay ninguna consulta a atender. 

El dato de **tiempo de respuesta de HH** tiene muchas implicaciones a nivel producto. Tener ese dato nos permite:
- informarle a la persona usuaria el tiempo promedio de respuesta antes de pasarla a hablar con une operadore, para que adecúe sus expectativas a la realidad. 
- informarle detalladamente este dato a los hospitales como reporte de uso al final del mes, para que organice al grupo de trabajo eficientemente y con información veraz
- permitir configurar lógicas automáticas de repartición de tareas para les operadores, para facilitarles su trabajo

Por ello lo que se pretende en este práctico es poder armar un modelo que nos ayude a predecir el tiempo de respuesta de HH. Lo que nos da este dato es la presencia de la feature Got_HH, que cuando vale 1 nos marca en el dataset que el bot realizó la transferencia. El siguiente mensaje que tenga Direction == outbound sería el primer mensaje de un operador humano. La diferencia de horas entre estos dos mensajes nos da el tiempo de respuesta de un operador humano.

Predecir esta variable teniendo en cuenta las distintas features del dataset será una tarea de regresión. Entrenar un modelo por hospital dará una mejor predicción. Por conocimiento del dataset sabemos que entrenar por porción del día (mañana/tarde) también dará mejores resultados, pero esto es opcional.

## Tareas
En orden,

Deberán armar un dataset más pequeño que el actual, **sacando**:
- las filas de los hospitales sin HH (Demo, Desarrollo, Clínica Carrá, Default) y las conversaciones sin HH (que agrupadas por conv_id no tengan un Got_HH == 1)
- las conversaciones que nunca hayan pasado a HH (es decir Got_HH es 0 en toda la agrupación por conv_id) (guiarse con https://stackoverflow.com/questions/52393659/pandas-dataframe-check-if-column-value-exists-in-a-group-of-columns )
- Para simplificar, las conversaciones que hayan pasado a HH pero el operador nunca respondió. Es decir Got_HH es 1 en alguna fila, pero no hay una fila siguiente con direction igual a outbound.

**generar** las features:

- tiempo_de_respuesta_HH (agrupando por conv_id, calcular el valor absoluto de la diferencia entre el SentDate del mensaje con Got_HH igual a 1 y el del siguiente mensaje con Direction igual a outbound https://stackoverflow.com/questions/34023918/make-new-column-in-panda-dataframe-by-adding-values-from-other-columns )
- cant de mensajes de la conversación (agrupación por conv_id+dia y luego sum) (https://stackoverflow.com/questions/39922986/how-do-i-pandas-group-by-to-get-sum)
- momento del dia (day_moment fue generada por el grupo 2 y puede reutilizarse el código que está aquí https://colab.research.google.com/drive/1KHgwiRqFLlavfhnCNdVvqG-xoPc0qMsM?usp=sharing#scrollTo=P04lwj2bSrFM )

**manteniendo** las features:

> - dia de la semana
> - fecha
> - presencia de errores en la conversación
> - hospital
> - cancelled
> - consulted
> - no correlation
> - y en general, todas las features que no sean body ni direction.
> - Debiendo quedar una fila por conversación.

* Cargar los datos, separando del dataset la etiqueta a predecir.
* Dividir el dataset en el conjunto de entrenamiento y conjunto de test
* Elegir y fundamentar si usar regresión lineal o polinomial(https://towardsdatascience.com/introduction-to-linear-regression-and-polynomial-regression-f8adc96f31cb, https://data36.com/polynomial-regression-python-scikit-learn/ ) . Tomarse un tiempito en hacer esta decisión les será muy útil ya que es una decisión interesante para comunicar en el video que tengan que hacer a partir de este práctico.
* Entrenar y evaluar un modelo de regresión lineal y uno polinomial, fijando la semilla aleatoria para hacer repetible el experimento.
* En cuanto a los hiper-parámetros:

        1.   Probar primero con los default y elegir alguna/s métrica/s para reportar los resultados. 
        2.   Luego usar grid-search (https://machinelearningmastery.com/hyperparameter-optimization-with-random-search-and-grid-search/) para explorar muchas combinaciones posibles de valores (Ejemplo de uso de grid search para encontrar el grado de polynomial regression https://stackoverflow.com/a/62460485/13597482 ). Reportar MAE y RMSE para las variaciones que busquen.

*   Para la mejor configuración encontrada, evaluar sobre el conjunto de entrenamiento y sobre el conjunto de evaluación, reportando MAE y RMSE.

### Se evaluarán los siguientes aspectos:
  ***1-*** Que se apliquen los conceptos vistos con los profes en el teórico y en el práctico.

  ***2-*** Capacidad de análisis. Enfocarse en esto les permitirá completar el video que deben preparar a continuación.

  ***3-*** Criterio para elegir que solución aplicar en cada caso y con qué método implementarla.


  
## Deadline pautado para la entrega: Miércoles 21/09/2022

Es importante que vayan anotando **conclusiones y observaciones en lenguaje natural** (no muy extensas) a medida que vayan realizando las tareas para que les sirva como **punto de partida para el video** de 10 min que se realice a partir de este práctico. El video que sigue a este práctico serviría como informe de resultados y observaciones de este práctico, resaltando aprendizajes y problemáticas con las que se hayan encontrado.

Lo importante de este práctico **no es encontrar el mejor modelo posible** ni mucho menos, sino poder ejercitar todo el proceso, que implica tanto **preparar los datos hasta correr los experimentos**, y finalmente **analizar y explicar los resultados encontrados**. En mi experiencia, la primera reacción ante saber que hay que comunicar resultados es querer comunicar éxitos, pero los resultados exitosos son -la mayoría de las veces- poco informativos. En el proceso de realización del práctico se encontrarán con desafíos de las tareas propuestas y con problemas específicos de este tipo de datasets conversacionales. Esa información es la valiosa a comunicar ya que es una experiencia que ningún otro grupo pudo tener, y le puede servir a otro grupo en un futuro que se relacione con datos que tengan características parecidas.

# Resolución

In [1]:
import pandas as pd
import numpy as np
import seaborn
import matplotlib
import matplotlib.pyplot as plt



In [2]:
file_key_marzo = 'marzo_anon_test.csv'
file_key_febrero = 'febrero_anon_test.csv'

file_key_procesado = 'dataset_post_entrega_2.csv'

df_marzo = pd.read_csv(file_key_marzo)
df_febrero = pd.read_csv(file_key_febrero)

In [67]:
df = pd.concat([df_febrero, df_marzo]).drop(['Unnamed: 0'], axis=1)
df['SentDate'] = pd.to_datetime(df.SentDate)


In [68]:
df.columns

Index(['Hospital', 'Tel_hospital', 'Body', 'Status', 'SentDate', 'Fecha',
       'Dia', 'Mes', 'Hora', 'Messages', 'Direction', 'Appointment_msp',
       'Appointment', 'Cancellation_msp', 'Cancelled', 'consult',
       'Consult_Appoint', 'fail_HH_sms', 'Fail_HH', 'achieve_HH', 'Got_HH',
       'Cupo', 'Full_turnos_obra_social', 'No_Relation', 'No_Correlation',
       'has_error', 'Error_Interno', 'has_error_501', 'Error_501',
       'falla_api_externo', 'Falla_Api_Externo', 'alta_dni', 'not_DNI',
       'issue_name', 'Issue_Name', 'ask_kunan', 'Ask_Kunan',
       'many_fallbacks_goto_hh', 'Many_Fallbacks_Goto_HH', 'conv_id'],
      dtype='object')

### ¿Cómo se ven los mensajes de _Human Handoff_?
Buscamos una muestra de los mensajes que nos interesan, solo para ver que forma tienen

In [69]:
df_handoffed = df[df['Got_HH'] == 1]
df_handoffed[['conv_id', 'Body', 'Hospital', 'Direction']]

conv_id                                               Body  \
164          10  Fuiste transferido a un humano, por favor escr...   
408          26  Fuiste transferido a un humano, por favor escr...   
518          32  Fuiste transferido a un humano, por favor escr...   
609          34  Fuiste transferido a un humano, por favor escr...   
666          25  Fuiste transferido a un humano, por favor escr...   
...         ...                                                ...   
290219     4596  Fuiste transferido a un humano, por favor escr...   
290339     7341  Fuiste transferido a un humano, por favor escr...   
290660     7056  Fuiste transferido a un humano, por favor escr...   
290921     7325  Fuiste transferido a un humano, por favor escr...   
290986     7295  Fuiste transferido a un humano, por favor escr...   

                  Hospital     Direction  
164               CityBell  outbound-api  
408               CityBell  outbound-api  
518               CityBell  outbound-api  
609     Salud Consultorios  outbound-api  
666               CityBell  outbound-api  
...                    ...           ...  
290219            CityBell  outbound-api  
290339            CityBell  outbound-api  
290660            CityBell  outbound-api  
290921            CityBell  outbound-api  
290986            CityBell  outbound-api  

[2757 rows x 4 columns]

In [70]:
df_handoffed.Direction.value_counts()

outbound-api    2756
inbound            1
Name: Direction, dtype: int64

In [71]:
# Esto es un error ? 
df_handoffed[df_handoffed.Direction == 'inbound']

Hospital             Tel_hospital  \
197335  CityBell  whatsapp:+5492215137770   

                                                     Body    Status  \
197335  Fuiste transferido a un humano, por favor escr...  received   

                        SentDate       Fecha  Dia  Mes  Hora  Messages  ...  \
197335 2022-03-22 12:07:49+00:00  2022-03-22   22    3    12         1  ...   

       Falla_Api_Externo alta_dni  not_DNI issue_name  Issue_Name ask_kunan  \
197335                 0       []        0         []           0        []   

        Ask_Kunan many_fallbacks_goto_hh  Many_Fallbacks_Goto_HH conv_id  
197335          0                     []                       0    4238  

[1 rows x 40 columns]

### ¿Cómo se vé una conversación que finaliza en _Human Handoff_?


In [72]:
# Elegimos una conversación cualquiera, vemos que intercambio de mensajes hay
df[df['conv_id'] == 32][['Body','Direction','SentDate','Got_HH']].sort_values(by='SentDate')

Body     Direction  \
6442                                                XXX       inbound   
6437                                      XXXXXXXXXXXXX       inbound   
6436  Hola, soy el asistente virtual de Centro Medic...  outbound-api   
6422                                     Sacar un turno       inbound   
6421                        Necesito tu DNI, por favor.  outbound-api   
...                                                 ...           ...   
875                                               204.0       inbound   
874   Por la opción elegida, te transferiré con una ...  outbound-api   
873   Para las siguientes prácticas comunicate a los...  outbound-api   
871   Hola, soy el asistente virtual de Clinica Carr...  outbound-api   
872   Estamos fuera del horario de atención con oper...  outbound-api   

                      SentDate  Got_HH  
6442 2022-02-16 11:45:35+00:00       0  
6437 2022-02-16 11:45:44+00:00       0  
6436 2022-02-16 11:45:45+00:00       0  
6422 2022-02-16 11:46:04+00:00       0  
6421 2022-02-16 11:46:04+00:00       0  
...                        ...     ...  
875  2022-03-01 15:50:13+00:00       0  
874  2022-03-01 15:50:13+00:00       0  
873  2022-03-01 15:50:13+00:00       0  
871  2022-03-01 15:50:14+00:00       0  
872  2022-03-01 15:50:14+00:00       0  

[78 rows x 4 columns]

## Filtro de conversaciones

In [187]:
def with_human_handoff(df):
  """
  Filter conversations which where 'human handoffed'
  The resulting dataframe is indexed by conv_id
  """
  c = df.groupby(by = ['conv_id'])[['Got_HH']].sum()
  return c[c.Got_HH > 0 ]

In [188]:
hhs = with_human_handoff(df_handoffed)
hhs[hhs.Got_HH > 1]

Got_HH
conv_id        
21            3
22            2
26            2
32            2
35            2
...         ...
6938          2
7029          2
7258          2
7292          2
7312          2

[454 rows x 1 columns]

### Conversaciones con mas de un pasaje a humano

TBD

### Seguimos mirando

In [189]:
# df = df.filter(items = [2,5], axis=0)
#df_hh = df.filter(items = hhs.index.values, axis=0)

merged = pd.merge(hhs, df, left_index=True, right_on='conv_id', suffixes = ('_sum', '_ori')).sort_values(by='SentDate')


merged[merged.Got_HH_sum == 1].sample(1)[['Got_HH_sum', 'Got_HH_ori']]


Got_HH_sum  Got_HH_ori
38265           1           0

In [239]:
# Todos estos mensajes pertenecen a conversaciones en las que se pidió HH
merged = merged.rename (columns = {"Got_HH_ori": "Got_HH"})

## Hay conversaciones que no tienen handoff, que pasaron el filtro
ds = merged.groupby(by = ['conv_id', 'Hospital'])[['Got_HH']].sum() > 0
ds = ds[ds.Got_HH]

Quiero
* Agrupar por conv_id
* Para cada conversacion:
** Buscar el mensaje con Got_HH == 1
** Obtener el siguiente



Features que necesitamos

        dia de la semana
        fecha
        presencia de errores en la conversación
        hospital
        cancelled
        consulted
        no correlation
        y en general, todas las features que no sean body ni direction.
        Debiendo quedar una fila por conversación.



In [192]:
def xyz(df):
  """
  Filter conversations which where 'human handoffed'
  The resulting dataframe is indexed by conv_id
  """
  return df.groupby(by = ['conv_id', 'Hospital'])

gs = xyz(merged)

gs['Hospital'].count()

conv_id  Hospital          
7        Carra                  23
         Salud Consultorios     61
10       CityBell               16
         Salud Consultorios     15
11       Carra                 262
                              ... 
7410     Salud Consultorios     22
7422     Salud Consultorios     28
7424     Salud Consultorios     26
7438     CityBell               13
7459     CityBell               13
Name: Hospital, Length: 3285, dtype: int64

In [229]:
def handle_conversation(conv_df):
    """
    Todos los mensajes en conv_df deben pertenecer a la misma conversación (y mismo hospital)
    """
    
    # human handoff request
    hh = conv_df[conv_df.Got_HH == 1]
    
    if len(hh) == 1:
        idx, hospital, conv_id, sent_date = hh.index.values[0], hh.Hospital, hh.conv_id, hh.SentDate
#        print(f"{i}: {hospital}/{conv_id} {sent_date}")
        
        #human handoff response
        r = conv_df[(conv_df.Direction == 'outbound-api') & (conv_df.index > i)]
        if len(r):
            first = r.head(0)
            print(first.SentDate - sent_date)
#        print(hh[0])
#         print(f"{msg_from.conv_id}/{msg_from.Hospital} {msg_from.SentDate}")
#         ffrom = msg_from.SentDate        
#         maybe_to = conv_df[(msg_from.index > msg_from.index) & (conv_df.Direction == 'outbound-api')]
#         if len(maybe_to) == 1:
#             to = maybe_to[0].SentDate
            
#             print(f"{ffrom} -> {to}")

#         print(hh.index)
    
    
    

for (conv_id, hospital), indices in gs.groups.items():

    conv_df = merged[(merged.conv_id == conv_id) & (merged.Hospital == hospital)].\
    sort_values(by='SentDate').reset_index(drop=True)
    
    print(conv_df[['SentDate','Direction', 'Got_HH']])
    print("---")
#     conv_df = merged.loc[indices.values].reset_index()
    #handle_conversation(conv_df)
    






                    SentDate     Direction  Got_HH
0  2022-02-16 19:46:14+00:00  outbound-api       0
1  2022-02-16 19:46:14+00:00       inbound       0
2  2022-02-17 10:08:05+00:00       inbound       0
3  2022-02-17 10:08:07+00:00  outbound-api       0
4  2022-02-17 10:08:07+00:00  outbound-api       0
5  2022-02-17 10:08:22+00:00       inbound       0
6  2022-02-17 10:08:24+00:00  outbound-api       0
7  2022-02-17 10:08:24+00:00  outbound-api       0
8  2022-02-17 10:09:06+00:00       inbound       0
9  2022-02-17 10:09:07+00:00  outbound-api       0
10 2022-02-17 10:09:22+00:00       inbound       0
11 2022-02-17 10:09:23+00:00  outbound-api       0
12 2022-02-17 10:09:23+00:00  outbound-api       0
13 2022-02-17 10:09:46+00:00       inbound       0
14 2022-02-17 10:09:48+00:00  outbound-api       0
15 2022-02-17 10:10:01+00:00       inbound       0
16 2022-02-17 10:10:03+00:00  outbound-api       0
17 2022-02-17 10:12:04+00:00       inbound       0
18 2022-02-17 10:12:05+00:00  o

                     SentDate     Direction  Got_HH
0   2022-03-01 16:34:05+00:00       inbound       0
1   2022-03-01 16:34:06+00:00  outbound-api       0
2   2022-03-01 16:34:06+00:00  outbound-api       0
3   2022-03-01 16:34:21+00:00       inbound       0
4   2022-03-01 16:34:21+00:00  outbound-api       0
..                        ...           ...     ...
157 2022-03-23 10:06:49+00:00  outbound-api       0
158 2022-03-23 10:06:50+00:00  outbound-api       0
159 2022-03-23 10:06:50+00:00  outbound-api       0
160 2022-03-23 10:06:50+00:00  outbound-api       0
161 2022-03-23 10:08:12+00:00       inbound       0

[162 rows x 3 columns]
---
                     SentDate     Direction  Got_HH
0   2022-02-16 12:48:39+00:00       inbound       0
1   2022-02-16 12:48:40+00:00  outbound-api       0
2   2022-02-16 12:48:52+00:00       inbound       0
3   2022-02-16 12:48:53+00:00  outbound-api       0
4   2022-02-16 12:49:18+00:00       inbound       0
..                        ...       

                     SentDate     Direction  Got_HH
0   2022-02-16 14:02:47+00:00  outbound-api       0
1   2022-02-16 14:02:47+00:00       inbound       0
2   2022-02-16 14:03:04+00:00       inbound       0
3   2022-02-16 14:03:13+00:00  outbound-api       0
4   2022-02-16 14:03:26+00:00       inbound       0
..                        ...           ...     ...
133 2022-02-16 15:39:32+00:00  outbound-api       0
134 2022-02-16 15:39:32+00:00       inbound       0
135 2022-02-16 15:41:29+00:00       inbound       0
136 2022-02-16 17:52:17+00:00  outbound-api       0
137 2022-02-16 17:52:39+00:00  outbound-api       0

[138 rows x 3 columns]
---
                    SentDate     Direction  Got_HH
0  2022-03-01 12:45:52+00:00       inbound       0
1  2022-03-01 12:45:52+00:00  outbound-api       0
2  2022-03-01 12:46:19+00:00       inbound       0
3  2022-03-01 12:46:20+00:00  outbound-api       0
4  2022-03-01 12:46:26+00:00       inbound       0
5  2022-03-01 12:46:31+00:00  outbound-api

                    SentDate     Direction  Got_HH
0  2022-02-15 12:43:29+00:00       inbound       0
1  2022-02-15 12:43:33+00:00  outbound-api       0
2  2022-02-15 12:43:47+00:00  outbound-api       0
3  2022-02-15 12:43:47+00:00       inbound       0
4  2022-02-15 12:44:42+00:00       inbound       0
5  2022-02-15 12:44:44+00:00  outbound-api       0
6  2022-02-15 12:44:44+00:00  outbound-api       0
7  2022-02-15 12:46:25+00:00       inbound       0
8  2022-02-15 12:46:27+00:00  outbound-api       0
9  2022-02-15 12:46:47+00:00  outbound-api       0
10 2022-02-15 12:46:47+00:00       inbound       0
11 2022-02-15 12:47:08+00:00       inbound       0
12 2022-02-15 12:47:09+00:00  outbound-api       0
13 2022-02-15 12:47:26+00:00       inbound       0
14 2022-02-15 12:47:27+00:00  outbound-api       0
15 2022-02-15 12:47:40+00:00       inbound       0
16 2022-02-15 12:47:41+00:00  outbound-api       0
17 2022-02-15 12:47:54+00:00       inbound       0
18 2022-02-15 12:47:55+00:00  o

                    SentDate     Direction  Got_HH
0  2022-03-02 19:38:29+00:00       inbound       0
1  2022-03-02 19:38:30+00:00  outbound-api       0
2  2022-03-02 19:52:31+00:00       inbound       0
3  2022-03-02 19:52:32+00:00  outbound-api       0
4  2022-03-02 19:52:40+00:00       inbound       0
5  2022-03-02 19:52:44+00:00  outbound-api       0
6  2022-03-02 19:52:44+00:00  outbound-api       0
7  2022-03-02 19:53:02+00:00       inbound       0
8  2022-03-02 19:53:03+00:00  outbound-api       0
9  2022-03-02 19:53:28+00:00       inbound       0
10 2022-03-02 19:53:29+00:00  outbound-api       0
11 2022-03-02 19:53:29+00:00  outbound-api       0
12 2022-03-02 19:53:42+00:00       inbound       0
13 2022-03-02 19:53:44+00:00  outbound-api       0
14 2022-03-02 19:53:55+00:00       inbound       0
15 2022-03-02 19:53:56+00:00  outbound-api       0
16 2022-03-02 19:54:05+00:00       inbound       0
17 2022-03-02 19:54:06+00:00  outbound-api       0
18 2022-03-02 19:54:06+00:00  o

...

                    SentDate     Direction  Got_HH
0  2022-03-30 13:42:00+00:00       inbound       0
1  2022-03-30 13:42:01+00:00  outbound-api       0
2  2022-03-30 13:42:27+00:00  outbound-api       0
3  2022-03-30 13:42:27+00:00       inbound       0
4  2022-03-30 13:42:34+00:00       inbound       0
5  2022-03-30 13:42:36+00:00  outbound-api       0
6  2022-03-30 13:42:37+00:00  outbound-api       0
7  2022-03-30 13:43:19+00:00       inbound       0
8  2022-03-30 13:43:20+00:00  outbound-api       0
9  2022-03-30 13:43:55+00:00       inbound       0
10 2022-03-30 13:43:57+00:00  outbound-api       0
11 2022-03-30 13:43:57+00:00  outbound-api       0
12 2022-03-30 13:44:12+00:00       inbound       0
13 2022-03-30 13:44:13+00:00  outbound-api       0
14 2022-03-30 13:44:55+00:00  outbound-api       1
15 2022-03-30 13:44:55+00:00  outbound-api       0
16 2022-03-30 13:44:55+00:00       inbound       0
17 2022-03-30 13:45:38+00:00       inbound       0
18 2022-03-30 13:50:25+00:00  o

                    SentDate     Direction  Got_HH
0  2022-03-30 16:30:41+00:00  outbound-api       0
1  2022-03-30 16:30:41+00:00       inbound       0
2  2022-03-30 16:31:44+00:00       inbound       0
3  2022-03-30 16:31:45+00:00  outbound-api       0
4  2022-03-30 16:31:52+00:00       inbound       0
5  2022-03-30 16:31:54+00:00  outbound-api       0
6  2022-03-30 16:31:54+00:00  outbound-api       0
7  2022-03-31 08:33:27+00:00       inbound       0
8  2022-03-31 08:33:28+00:00  outbound-api       0
9  2022-03-31 08:33:28+00:00  outbound-api       0
10 2022-03-31 08:33:28+00:00  outbound-api       0
11 2022-03-31 08:35:02+00:00       inbound       0
12 2022-03-31 08:35:03+00:00  outbound-api       0
13 2022-03-31 08:35:03+00:00  outbound-api       1
14 2022-03-31 08:35:12+00:00       inbound       0
15 2022-03-31 08:52:06+00:00       inbound       0
16 2022-03-31 10:04:21+00:00       inbound       0
17 2022-03-31 15:26:32+00:00  outbound-api       0
18 2022-03-31 15:26:36+00:00  o

                    SentDate     Direction  Got_HH
0  2022-03-30 13:27:51+00:00       inbound       0
1  2022-03-30 13:27:51+00:00  outbound-api       0
2  2022-03-30 13:28:28+00:00       inbound       0
3  2022-03-30 13:28:29+00:00  outbound-api       0
4  2022-03-30 13:28:36+00:00       inbound       0
5  2022-03-30 13:28:38+00:00  outbound-api       0
6  2022-03-30 13:28:38+00:00  outbound-api       0
7  2022-03-30 13:28:59+00:00       inbound       0
8  2022-03-30 13:28:59+00:00  outbound-api       0
9  2022-03-30 13:29:07+00:00       inbound       0
10 2022-03-30 13:29:08+00:00  outbound-api       0
11 2022-03-30 13:29:09+00:00  outbound-api       0
12 2022-03-30 13:29:09+00:00  outbound-api       0
13 2022-03-30 13:29:45+00:00       inbound       0
14 2022-03-30 13:29:47+00:00  outbound-api       0
15 2022-03-30 13:29:47+00:00  outbound-api       0
16 2022-03-30 13:29:47+00:00  outbound-api       1
---
                    SentDate     Direction  Got_HH
0  2022-03-30 12:35:29+00:0

                    SentDate     Direction  Got_HH
0  2022-03-31 18:23:05+00:00       inbound       0
1  2022-03-31 18:23:06+00:00  outbound-api       0
2  2022-03-31 18:23:24+00:00       inbound       0
3  2022-03-31 18:23:25+00:00  outbound-api       0
4  2022-03-31 18:23:34+00:00       inbound       0
5  2022-03-31 18:23:35+00:00  outbound-api       0
6  2022-03-31 18:23:43+00:00       inbound       0
7  2022-03-31 18:23:45+00:00  outbound-api       0
8  2022-03-31 18:23:46+00:00  outbound-api       0
9  2022-03-31 18:24:06+00:00       inbound       0
10 2022-03-31 18:24:07+00:00  outbound-api       0
11 2022-03-31 18:24:16+00:00  outbound-api       0
12 2022-03-31 18:24:16+00:00  outbound-api       0
13 2022-03-31 18:24:16+00:00       inbound       0
14 2022-03-31 18:25:05+00:00       inbound       0
15 2022-03-31 18:25:06+00:00  outbound-api       0
16 2022-03-31 18:25:06+00:00  outbound-api       1
17 2022-03-31 18:25:06+00:00  outbound-api       0
18 2022-03-31 18:25:56+00:00   

                    SentDate     Direction  Got_HH
0  2022-03-31 15:31:08+00:00  outbound-api       0
1  2022-03-31 15:31:08+00:00       inbound       0
2  2022-03-31 15:31:29+00:00       inbound       0
3  2022-03-31 15:31:30+00:00  outbound-api       0
4  2022-03-31 15:31:38+00:00       inbound       0
5  2022-03-31 15:31:41+00:00  outbound-api       0
6  2022-03-31 15:31:41+00:00  outbound-api       0
7  2022-03-31 15:31:57+00:00       inbound       0
8  2022-03-31 15:31:58+00:00  outbound-api       0
9  2022-03-31 15:32:08+00:00  outbound-api       0
10 2022-03-31 15:32:08+00:00       inbound       0
11 2022-03-31 15:32:09+00:00  outbound-api       0
12 2022-03-31 15:32:09+00:00  outbound-api       0
13 2022-03-31 16:38:27+00:00  outbound-api       0
14 2022-03-31 16:38:27+00:00  outbound-api       0
15 2022-03-31 16:38:27+00:00       inbound       0
16 2022-03-31 16:38:28+00:00  outbound-api       0
17 2022-03-31 16:38:28+00:00  outbound-api       0
18 2022-03-31 16:41:37+00:00  o